In [ ]:
# ..... devCellPy mouse data ..... #

In [22]:
library(Seurat)
library(SingleCellExperiment)
library(MetaNeighbor)
library(dplyr)

In [60]:
# get ortholog gene list
om = read.delim('mouse_chicken_orthologs_biomart.txt', sep = '\t')
om <- om[om[,1]!='' & om[,2]!='' & om[,4]=='ortholog_one2one',]
dim(om)
om[1,]

[1] 12287     4

Gene.name Chicken.gene.name Last.common.ancestor.with.Chicken
6 mt-Nd1    ND1               Amniota                          
  Chicken.homology.type
6 ortholog_one2one

In [27]:
# load mouse-dev data
sc = readRDS('~/septation/cardiac_atlas_seurat_object.rds')
keepids = which(sc$Timepoint %in% c('E9.25', 'E10.5', 'E13.5'))

# add other features to metadata
sc$sample = sc$Batch
sc$stage = sc$Timepoint
sc$cluster = sc$Celltype1
sc$celltype = sc$Celltype1
sc$species = 'mouse'
sc

An object of class Seurat 
30439 features across 104199 samples within 1 assay 
Active assay: RNA (30439 features, 0 variable features)
 2 dimensional reductions calculated: mnn, umap

In [39]:
# load data
get_seurat_obj <- function(currstage1){
    
    sc1 = readRDS(paste0(currstage1, '_integrated_cca.rds'))

    df1 = read.delim(paste0(currstage1, '_cluster_anno_Knight-Schrijver.csv'), sep = ',')
    ids = match(rownames(sc1@meta.data), df1$barcode)
    sc1$metacell = df1$metacell[ids]
    sc1$celltype = df1$consensus_type[ids]
    sc1$cluster = df1$cluster[ids]

    sc1$stage <- sc1$orig.ident
    sc1 <- sc1[,!is.na(sc1$celltype)]
    sc1$species = 'chicken'
    return(sc1)
}

In [40]:
# load individual sample files
stage1 = 'stage23'
sce1 = get_seurat_obj(stage1)

# get metadata
cols = c('species', 'stage', 'sample', 'celltype', 'cluster')
mtd0 = sce1@meta.data[,cols]

In [48]:
id1 = intersect(match(rownames(sc), om[,1]), match(rownames(sce1), om[,2]))
id1 = id1[!is.na(id1)]
length(id1)
common_genes 

[1] 2380

ERROR: Error in eval(expr, envir, enclos): object 'common_genes' not found


In [53]:
# which(is.na(match(rownames(sce1), om[,2])))
rownames(sce1)[55:58]

[1] "ENSGALG00010015122" "DMD"                "GRM8"              
[4] "SCN5A"

In [59]:
which(om[,2]=='SCN5A')

integer(0)

In [55]:
match('Scn5a', rownames(sc))

[1] 11268

In [26]:


# make SCE object
sce = SingleCellExperiment(list(counts = sce1@assays$RNA@counts),
                           colData = DataFrame(mtd0))

options(warn = -1)
start.time <- Sys.time()
hvg = variableGenes(sce, exp_labels = sce$sample)

# defaults to top 95% of genes. May need to vary
end.time <- Sys.time()
time.taken <- end.time - start.time
time.taken

# get top 2k hvgs
if(length(hvg)>2000){
    hvg <- sample(hvg, 2000, replace = F)
}

orig.ident          nCount_RNA nFeature_RNA Batch       
AGGGATGAGACTTGAA-1_2_2 deSoysa_e825_batch2 32284.257  5600         batch_e825_2
AGGGATGCAAGCGATG-1_2_2 deSoysa_e825_batch2 21509.373  4371         batch_e825_2
AGGGATGCAATCGGTT-1_2_2 deSoysa_e825_batch2 14094.181  3647         batch_e825_2
AGGGATGGTCACCTAA-1_2_2 deSoysa_e825_batch2 14837.532  3734         batch_e825_2
AGGGATGGTCCGAAGA-1_2_2 deSoysa_e825_batch2 17018.538  3989         batch_e825_2
AGGGATGGTCTGATCA-1_2_2 deSoysa_e825_batch2 21565.141  4759         batch_e825_2
AGGGATGTCAGCGACC-1_2_2 deSoysa_e825_batch2 11952.151  3575         batch_e825_2
AGGGATGTCTTGCCGT-1_2_2 deSoysa_e825_batch2 23054.280  4880         batch_e825_2
AGGGTGAAGACTGGGT-1_2_2 deSoysa_e825_batch2 17895.200  4187         batch_e825_2
AGGGTGAAGCCCTAAT-1_2_2 deSoysa_e825_batch2 19325.824  4604         batch_e825_2
AGGGTGAAGTGCGTGA-1_2_2 deSoysa_e825_batch2 13427.608  3628         batch_e825_2
AGGGTGACAACACCCG-1_2_2 deSoysa_e825_batch2 17861.284  4255         batch_e825_2
AGGGTGACACGTCTCT-1_2_2 deSoysa_e825_batch2 19084.229  4387         batch_e825_2
AGGGTGACATATGAGA-1_2_2 deSoysa_e825_batch2 16569.734  4135         batch_e825_2
AGGGTGAGTTCGCGAC-1_2_2 deSoysa_e825_batch2 15795.641  3934         batch_e825_2
AGGGTGATCCTTGACC-1_2_2 deSoysa_e825_batch2 13721.454  3826         batch_e825_2
AGGGTGATCGCAAGCC-1_2_2 deSoysa_e825_batch2 24831.697  4882         batch_e825_2
AGGGTGATCGGACAAG-1_2_2 deSoysa_e825_batch2 21637.638  4572         batch_e825_2
AGGGTGATCTTCAACT-1_2_2 deSoysa_e825_batch2 22955.513  4862         batch_e825_2
AGGTCATCACATCCGG-1_2_2 deSoysa_e825_batch2  9281.037  3010         batch_e825_2
AGGTCATCACATTTCT-1_2_2 deSoysa_e825_batch2 30978.387  5607         batch_e825_2
AGGTCATCACTGTCGG-1_2_2 deSoysa_e825_batch2  7001.348  2765         batch_e825_2
AGGTCATCAGACAGGT-1_2_2 deSoysa_e825_batch2 17084.026  4146         batch_e825_2
AGGTCATCATAGGATA-1_2_2 deSoysa_e825_batch2 13710.299  3721         batch_e825_2
AGGTCATCATGGTAGG-1_2_2 deSoysa_e825_batch2 16278.502  4171         batch_e825_2
AGGTCATCATTACCTT-1_2_2 deSoysa_e825_batch2 16542.441  4493         batch_e825_2
AGGTCATGTACCTACA-1_2_2 deSoysa_e825_batch2 20942.507  4643         batch_e825_2
AGGTCATGTATATGGA-1_2_2 deSoysa_e825_batch2 16572.642  4231         batch_e825_2
AGGTCATGTATGGTTC-1_2_2 deSoysa_e825_batch2 19963.488  4264         batch_e825_2
AGGTCATGTCGAATCT-1_2_2 deSoysa_e825_batch2 18198.112  4261         batch_e825_2
⋮                      ⋮                   ⋮          ⋮            ⋮           
cell_54090_7           cell                15189      3525         2           
cell_54091_7           cell                16104      3718         2           
cell_54093_7           cell                31875      5183         2           
cell_54096_7           cell                26424      4741         2           
cell_54099_7           cell                18570      3754         2           
cell_54103_7           cell                 8863      2794         2           
cell_54114_7           cell                38158      5324         2           
cell_54117_7           cell                16881      3721         2           
cell_54119_7           cell                19576      3996         2           
cell_54121_7           cell                18952      3850         2           
cell_54123_7           cell                19398      3953         2           
cell_54125_7           cell                15759      3757         2           
cell_54126_7           cell                13777      3456         2           
cell_54129_7           cell                13990      3514         2           
cell_54132_7           cell                15268      3545         2           
cell_54133_7           cell                16107      3660         2           
cell_54135_7           cell                13299      3532         2           
cell_54137_7           cell                11981      3302         2           
cell_54138_7           